In [16]:
import numpy as np
import pandas as pd

from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objects as go
init_notebook_mode(connected=True)



In [17]:
df= pd.read_csv('Marketing-Customer-Value-Analysis.csv', low_memory=False)
df.head()

Customer       State  Customer Lifetime Value Response  Coverage Education  \
0  BU79786  Washington              2763.519279       No     Basic  Bachelor   
1  QZ44356     Arizona              6979.535903       No  Extended  Bachelor   
2  AI49188      Nevada             12887.431650       No   Premium  Bachelor   
3  WW63253  California              7645.861827       No     Basic  Bachelor   
4  HB64268  Washington              2813.692575       No     Basic  Bachelor   

  Effective To Date EmploymentStatus Gender  Income  ...  \
0           2/24/11         Employed      F   56274  ...   
1           1/31/11       Unemployed      F       0  ...   
2           2/19/11         Employed      F   48767  ...   
3           1/20/11       Unemployed      M       0  ...   
4            2/3/11         Employed      M   43836  ...   

  Months Since Policy Inception Number of Open Complaints  Number of Policies  \
0                             5                         0                   1   
1                            42                         0                   8   
2                            38                         0                   2   
3                            65                         0                   7   
4                            44                         0                   1   

      Policy Type        Policy  Renew Offer Type  Sales Channel  \
0  Corporate Auto  Corporate L3            Offer1          Agent   
1   Personal Auto   Personal L3            Offer3          Agent   
2   Personal Auto   Personal L3            Offer1          Agent   
3  Corporate Auto  Corporate L2            Offer1    Call Center   
4   Personal Auto   Personal L1            Offer1          Agent   

  Total Claim Amount  Vehicle Class Vehicle Size  
0         384.811147   Two-Door Car      Medsize  
1        1131.464935  Four-Door Car      Medsize  
2         566.472247   Two-Door Car      Medsize  
3         529.881344            SUV      Medsize  
4         138.130879  Four-Door Car      Medsize  

[5 rows x 24 columns]

In [18]:
df.shape

(9134, 24)

Exploratory Data Analysis (EDA) with Plotly


In [5]:
import plotly.express as px

fig = px.histogram(df, x='Sales Channel', color='Response')

fig.show()

In [6]:
fig = px.histogram(df, x='Renew Offer Type', color='Response')

fig.show()

Now let’s explore some demographic information to see what types of customers are most likely to respond to our marketing offers

In [7]:
fig = px.histogram(df, x="Education", color='Response')
fig.show()

fig = px.histogram(df, x="Vehicle Class", color='Response')
fig.show()

How can we further explore the seemingly negative correlation between wealth and response rate?



In [8]:
df = df[df['Income'] > 0] #Drop rows where income data not available

fig = px.violin(df, y="Income", x="Response", 
                box=True, points="all", hover_data=df.columns, 
                title = 'Response Rate by Income')
fig.show()

In this case, we will be using Logistic Regression to determine which variables, if any, have an influence on the probability of the customer responding to a sales call.

In [19]:
df.shape

(9134, 24)

In [20]:
import statsmodels.api as sm

df.Response = df.Response.apply(lambda X : 0 if X == 'No' else 1) #Make Response a continuous value

cont_df = df.select_dtypes(include=['int64','float']) #Create dataframe with only continuous variables

cont_reg = sm.Logit(cont_df['Response'], cont_df.drop('Response', axis = 1))
cont_reg.fit().summary()



Optimization terminated successfully.
         Current function value: 0.421189
         Iterations 6


<class 'statsmodels.iolib.summary.Summary'>
"""
                           Logit Regression Results                           
==============================================================================
Dep. Variable:               Response   No. Observations:                 9134
Model:                          Logit   Df Residuals:                     9126
Method:                           MLE   Df Model:                            7
Date:                Mon, 31 Jul 2023   Pseudo R-squ.:                -0.02546
Time:                        15:38:44   Log-Likelihood:                -3847.1
converged:                       True   LL-Null:                       -3751.6
Covariance Type:            nonrobust   LLR p-value:                     1.000
=================================================================================================
                                    coef    std err          z      P>|z|      [0.025      0.975]
-------------------------------------------------------------------------------------------------
Customer Lifetime Value       -6.741e-06   5.04e-06     -1.337      0.181   -1.66e-05    3.14e-06
Income                        -2.857e-06   1.03e-06     -2.766      0.006   -4.88e-06   -8.33e-07
Monthly Premium Auto             -0.0084      0.001     -6.889      0.000      -0.011      -0.006
Months Since Last Claim          -0.0202      0.003     -7.238      0.000      -0.026      -0.015
Months Since Policy Inception    -0.0060      0.001     -6.148      0.000      -0.008      -0.004
Number of Open Complaints        -0.0829      0.034     -2.424      0.015      -0.150      -0.016
Number of Policies               -0.0810      0.013     -6.356      0.000      -0.106      -0.056
Total Claim Amount                0.0001      0.000      0.711      0.477      -0.000       0.000
=================================================================================================
"""

In [21]:
categorical_df = df.select_dtypes(include='object')

cat_df = categorical_df.drop(['Customer', 'Effective To Date'], axis=1)

cols=cat_df.columns.tolist()

In [22]:
cols

['State',
 'Coverage',
 'Education',
 'EmploymentStatus',
 'Gender',
 'Location Code',
 'Marital Status',
 'Policy Type',
 'Policy',
 'Renew Offer Type',
 'Sales Channel',
 'Vehicle Class',
 'Vehicle Size']

In [23]:
cols=cat_df.columns.tolist()

from sklearn.preprocessing import LabelEncoder
for col in cat_df[cols]:
    cat_df[col] = LabelEncoder().fit_transform(cat_df[col])

In [24]:
categorical_train = sm.Logit(cont_df.Response, cat_df)
categorical_train.fit().summary()

Optimization terminated successfully.
         Current function value: 0.387557
         Iterations 7


<class 'statsmodels.iolib.summary.Summary'>
"""
                           Logit Regression Results                           
==============================================================================
Dep. Variable:               Response   No. Observations:                 9134
Model:                          Logit   Df Residuals:                     9121
Method:                           MLE   Df Model:                           12
Date:                Mon, 31 Jul 2023   Pseudo R-squ.:                 0.05642
Time:                        16:43:56   Log-Likelihood:                -3539.9
converged:                       True   LL-Null:                       -3751.6
Covariance Type:            nonrobust   LLR p-value:                 4.224e-83
====================================================================================
                       coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------------
State               -0.0256      0.023     -1.122      0.262      -0.070       0.019
Coverage            -0.0639      0.046     -1.390      0.164      -0.154       0.026
Education            0.0088      0.022      0.409      0.683      -0.033       0.051
EmploymentStatus    -0.0459      0.024     -1.951      0.051      -0.092       0.000
Gender               0.0466      0.060      0.774      0.439      -0.071       0.165
Location Code       -0.0477      0.047     -1.014      0.311      -0.140       0.045
Marital Status      -0.4643      0.047     -9.816      0.000      -0.557      -0.372
Policy Type          0.1736      0.132      1.311      0.190      -0.086       0.433
Policy              -0.0751      0.037     -2.033      0.042      -0.147      -0.003
Renew Offer Type    -0.5681      0.037    -15.226      0.000      -0.641      -0.495
Sales Channel       -0.2150      0.030     -7.148      0.000      -0.274      -0.156
Vehicle Class        0.0201      0.015      1.381      0.167      -0.008       0.049
Vehicle Size        -0.3355      0.052     -6.398      0.000      -0.438      -0.233
====================================================================================
"""

In [25]:
cont_df

Customer Lifetime Value  Response  Income  Monthly Premium Auto  \
0                 2763.519279         0   56274                    69   
1                 6979.535903         0       0                    94   
2                12887.431650         0   48767                   108   
3                 7645.861827         0       0                   106   
4                 2813.692575         0   43836                    73   
...                       ...       ...     ...                   ...   
9129             23405.987980         0   71941                    73   
9130              3096.511217         1   21604                    79   
9131              8163.890428         0       0                    85   
9132              7524.442436         0   21941                    96   
9133              2611.836866         0       0                    77   

      Months Since Last Claim  Months Since Policy Inception  \
0                          32                              5   
1                          13                             42   
2                          18                             38   
3                          18                             65   
4                          12                             44   
...                       ...                            ...   
9129                       18                             89   
9130                       14                             28   
9131                        9                             37   
9132                       34                              3   
9133                        3                             90   

      Number of Open Complaints  Number of Policies  Total Claim Amount  
0                             0                   1          384.811147  
1                             0                   8         1131.464935  
2                             0                   2          566.472247  
3                             0                   7          529.881344  
4                             0                   1          138.130879  
...                         ...                 ...                 ...  
9129                          0                   2          198.234764  
9130                          0                   1          379.200000  
9131                          3                   2          790.784983  
9132                          0                   3          691.200000  
9133                          0                   1          369.600000  

[9134 rows x 9 columns]

In [26]:
cont_df.reset_index(drop = True, inplace=True)
cont_df

Customer Lifetime Value  Response  Income  Monthly Premium Auto  \
0                 2763.519279         0   56274                    69   
1                 6979.535903         0       0                    94   
2                12887.431650         0   48767                   108   
3                 7645.861827         0       0                   106   
4                 2813.692575         0   43836                    73   
...                       ...       ...     ...                   ...   
9129             23405.987980         0   71941                    73   
9130              3096.511217         1   21604                    79   
9131              8163.890428         0       0                    85   
9132              7524.442436         0   21941                    96   
9133              2611.836866         0       0                    77   

      Months Since Last Claim  Months Since Policy Inception  \
0                          32                              5   
1                          13                             42   
2                          18                             38   
3                          18                             65   
4                          12                             44   
...                       ...                            ...   
9129                       18                             89   
9130                       14                             28   
9131                        9                             37   
9132                       34                              3   
9133                        3                             90   

      Number of Open Complaints  Number of Policies  Total Claim Amount  
0                             0                   1          384.811147  
1                             0                   8         1131.464935  
2                             0                   2          566.472247  
3                             0                   7          529.881344  
4                             0                   1          138.130879  
...                         ...                 ...                 ...  
9129                          0                   2          198.234764  
9130                          0                   1          379.200000  
9131                          3                   2          790.784983  
9132                          0                   3          691.200000  
9133                          0                   1          369.600000  

[9134 rows x 9 columns]

In [27]:
cont_df.reset_index(drop = True, inplace=True)
cat_df.reset_index(drop = True, inplace=True)

combined_df = pd.concat([cont_df,cat_df], axis = 1)

combined_train = sm.Logit(combined_df.Response, combined_df.drop(['Response'], axis = 1))
combined_train.fit().summary()

Optimization terminated successfully.
         Current function value: 0.384709
         Iterations 7


<class 'statsmodels.iolib.summary.Summary'>
"""
                           Logit Regression Results                           
==============================================================================
Dep. Variable:               Response   No. Observations:                 9134
Model:                          Logit   Df Residuals:                     9113
Method:                           MLE   Df Model:                           20
Date:                Mon, 31 Jul 2023   Pseudo R-squ.:                 0.06336
Time:                        16:51:28   Log-Likelihood:                -3513.9
converged:                       True   LL-Null:                       -3751.6
Covariance Type:            nonrobust   LLR p-value:                 4.066e-88
=================================================================================================
                                    coef    std err          z      P>|z|      [0.025      0.975]
-------------------------------------------------------------------------------------------------
Customer Lifetime Value       -1.183e-05   5.11e-06     -2.317      0.021   -2.18e-05   -1.82e-06
Income                         3.347e-06   1.39e-06      2.411      0.016    6.26e-07    6.07e-06
Monthly Premium Auto             -0.0033      0.001     -2.471      0.013      -0.006      -0.001
Months Since Last Claim          -0.0053      0.003     -1.780      0.075      -0.011       0.001
Months Since Policy Inception    -0.0019      0.001     -1.830      0.067      -0.004       0.000
Number of Open Complaints        -0.0569      0.035     -1.622      0.105      -0.126       0.012
Number of Policies               -0.0392      0.013     -3.013      0.003      -0.065      -0.014
Total Claim Amount                0.0007      0.000      4.448      0.000       0.000       0.001
State                            -0.0084      0.023     -0.357      0.721      -0.054       0.038
Coverage                         -0.0325      0.053     -0.615      0.538      -0.136       0.071
Education                         0.0235      0.022      1.068      0.285      -0.020       0.067
EmploymentStatus                 -0.0232      0.030     -0.763      0.445      -0.083       0.036
Gender                            0.0584      0.061      0.950      0.342      -0.062       0.179
Location Code                    -0.0894      0.053     -1.696      0.090      -0.193       0.014
Marital Status                   -0.4645      0.048     -9.585      0.000      -0.559      -0.370
Policy Type                       0.1085      0.135      0.806      0.420      -0.155       0.372
Policy                           -0.0335      0.039     -0.864      0.388      -0.110       0.043
Renew Offer Type                 -0.5828      0.039    -15.136      0.000      -0.658      -0.507
Sales Channel                    -0.1937      0.030     -6.354      0.000      -0.253      -0.134
Vehicle Class                     0.0287      0.015      1.897      0.058      -0.001       0.058
Vehicle Size                     -0.2837      0.055     -5.161      0.000      -0.391      -0.176
=================================================================================================
"""

In [28]:
y = combined_df.Response
X = combined_df.drop('Response', axis = 1)

from sklearn.model_selection import train_test_split, cross_validate

X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size = 0.2, random_state = 42)

In [29]:
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report
from sklearn.svm import SVC

svc = SVC(gamma='auto')
svc.fit(X_train, y_train)

svc_pred = svc.predict(X_test)




In [30]:
print(confusion_matrix(svc_pred,y_test))
print('accuracy_score:',accuracy_score(svc_pred, y_test))
print(classification_report(svc_pred, y_test))

[[1561   18]
 [   0  248]]
accuracy_score: 0.9901477832512315
              precision    recall  f1-score   support

           0       1.00      0.99      0.99      1579
           1       0.93      1.00      0.96       248

    accuracy                           0.99      1827
   macro avg       0.97      0.99      0.98      1827
weighted avg       0.99      0.99      0.99      1827



In [31]:
cross_val_score_svc = cross_validate(svc, X_train, y_train,cv = 5,return_train_score=True)
print('Cross validation train_score',cross_val_score_svc['train_score'].mean())
print('Cross validation test_score',cross_val_score_svc['test_score'])

Cross validation train_score 1.0
Cross validation test_score [0.98426813 0.9876881  0.98494182 0.98562628 0.98220397]
